# Text task notebook template
## Loading the necessary libraries

In [ ]:
from fastapi import APIRouter
from datetime import datetime
from datasets import load_dataset
from sklearn.metrics import accuracy_score
import random

import sys
sys.path.append('../tasks')

from utils.evaluation import AudioEvaluationRequest
from utils.emissions import tracker, clean_emissions_data, get_space_info


# Define the label mapping
LABEL_MAPPING = {
    "chainsaw": 0,
    "environment": 1
}

In [ ]:
from huggingface_hub import login
login()

## Loading the datasets and splitting them

In [ ]:
request = AudioEvaluationRequest()

# Load and prepare the dataset
dataset = load_dataset(request.dataset_name)

# Split dataset
train_test = dataset["train"].train_test_split(test_size=request.test_size, seed=request.test_seed)
test_dataset = train_test["test"]

In [ ]:
train_test.shape

## Random Baseline

In [8]:
# Start tracking emissions
tracker.start()
tracker.start_task("inference")

In [ ]:

#--------------------------------------------------------------------------------------------
# YOUR MODEL INFERENCE CODE HERE
# Update the code below to replace the random baseline by your model inference within the inference pass where the energy consumption and emissions are tracked.
#--------------------------------------------------------------------------------------------   

# Make random predictions (placeholder for actual model inference)
true_labels = test_dataset["label"]
predictions = [random.randint(0, 1) for _ in range(len(true_labels))]

predictions

#--------------------------------------------------------------------------------------------
# YOUR MODEL INFERENCE STOPS HERE
#--------------------------------------------------------------------------------------------   

In [ ]:
# Stop tracking emissions
emissions_data = tracker.stop_task()
emissions_data

In [ ]:
# Calculate accuracy
accuracy = accuracy_score(true_labels, predictions)
accuracy

In [ ]:
# Prepare results dictionary
results = {
    "submission_timestamp": datetime.now().isoformat(),
    "accuracy": float(accuracy),
    "energy_consumed_wh": emissions_data.energy_consumed * 1000,
    "emissions_gco2eq": emissions_data.emissions * 1000,
    "emissions_data": clean_emissions_data(emissions_data),
    "dataset_config": {
        "dataset_name": request.dataset_name,
        "test_size": request.test_size,
        "test_seed": request.test_seed
    }
}

results